# Signals and Datasets

**Signals** are time-series data sources in Vessim that can represent any value that changes over time - like solar irradiance, power consumption, or carbon intensity.

## What are Signals?

Signals can be used in two ways:
1. **Standalone** in your own projects for time-series analysis
2. **As input to Actors** in Vessim co-simulations to model realistic behavior

Vessim provides different signal types:
- `StaticSignal`: Returns a constant value for mocking and testing
- `Trace`: Replays historical datasets (solar data, carbon intensity, etc.)
- `PrometheusSignal`: Pulls energy usage data from a Prometheus instance
- `WatttimeSignal`: Pulls marginal carbon intensity data from the [WattTime API](https://watttime.org/)

In [14]:
import pandas as pd
import vessim as vs

# Required for running Mosaic in Jupyter notebooks (fixes asyncio event loop conflicts)
import nest_asyncio
nest_asyncio.apply()

## The StaticSignal

For testing and simple scenarios, the `StaticSignal` provides constant values:

In [2]:
server_load = vs.StaticSignal(value=-700)  # 700W server (negative = consumes power)

# Use in simulations
vs.Actor(name="server", signal=server_load)

# Direct use
server_load.now()

-700

## The Trace signal and Vessim's built-in datasets

Vessim comes with ready-to-use datasets that can be loaded directly into `vs.Trace` signals.
These datasets include real historical data for solar irradiance and carbon intensity.

### Solar Irradiance Data (Solcast)

- **Resolution**: 5-minute intervals
- **Forecast resolution**: 5 minutes (every 5 minutes a new forecast is available for the next 65 minutes so that there is at least one hour of forecasts available at all times)
- **Unit:** Fraction of maximum possible solar output normalized between 0 and 1 (can be scaled linearly with the output of the solar plant)
- **Fill-Method:** Backward-Fill (value is always valid for the 5 minutes before the timestamp)

**`solcast2022_global`**

Solar irradiance data for 10 major cities worldwide (June 8 - July 6, 2022)

- **Columns:** Berlin, Cape Town, Hong Kong, Lagos, Mexico City, Mumbai, San Francisco, Stockholm, Sydney, São Paulo 
- **Actual data:** 712kB (8353 rows, 11 columns)
- **Forecast data:** 10.9 MB (107342 rows, 12 columns)

In [3]:
global_trace = vs.Trace.load("solcast2022_global")
fig_global = vs.plot.plot_trace(global_trace, default_visible="Berlin", dataset_name="solcast2022_global")
fig_global.show()

**`solcast2022_germany`**

Solar irradiance data for the 10 largest German cities (July 15 - August 14, 2022)

- **Columns:** Berlin, Cologne, Dortmund, Düsseldorf, Essen, Frankfurt, Hamburg, Leipzig, Munich, Stuttgart
- **Actual data:** 798kB (8929 rows, 11 columns)
- **Forecast data:** 12.1 MB (114830 rows, 12 columns)

In [4]:
germany_trace = vs.Trace.load("solcast2022_germany")
fig_germany = vs.plot.plot_trace(germany_trace, default_visible="Berlin", dataset_name="solcast2022_germany")
fig_germany.show()

In [5]:
# Example: Load solar data for Mumbai and scale to 5kW solar panel
solar_signal = vs.Trace.load("solcast2022_global", params={"scale": 5000})  # 5kW max output
power_at_noon = solar_signal.now(at="2022-06-15T12:00:00", column="Mumbai")
print(f"Solar power at noon in Mumbai: {power_at_noon:.1f}W")

Solar power at noon in Mumbai: 950.8W


### Carbon Intensity Data (WattTime)

**`watttime2023_caiso-north`**
- Carbon intensity data for California (June 8 - July 8, 2023)
- **Resolution**: 5-minute intervals  
- **Unit**: grams CO2 per kWh (g/kWh)

In [6]:
carbon_signal = vs.Trace.load("watttime2023_caiso-north")
fig_carbon = vs.plot.plot_trace(carbon_signal)
fig_carbon.show()

In [7]:
# Example: Load carbon intensity data
carbon_signal = vs.Trace.load("watttime2023_caiso-north")
carbon_intensity = carbon_signal.now(at="2023-06-15T12:00:00", column="Caiso_North")
print(f"Carbon intensity at noon: {carbon_intensity:.1f} g/kWh")

Carbon intensity at noon: 427.3 g/kWh


## Creating a Custom Trace Signal

The `Trace` signal loads historical data from pandas DataFrames, where timestamps are the index and columns represent different locations or values.

In [8]:
actual = pd.DataFrame([
   ["2020-01-01T00:00:00", 100, 324],
   ["2020-01-01T00:30:00", 110, 357],
   ["2020-01-01T01:00:00", 105, 398],
], columns=["timestamp", "solar", "wind"])
actual = actual.set_index(["timestamp"])
signal = vs.Trace(actual)

In [9]:
signal.now(at="2020-01-01T00:00:00", column="solar")

np.float64(100.0)

You can also provide forecast data using a 2-level index (request time, forecast time):

In [10]:
forecast = pd.DataFrame([
   ["2020-01-01T00:00:00", "2020-01-01T00:30:00", 115, 370],
   ["2020-01-01T00:00:00", "2020-01-01T01:00:00", 108, 372],
   ["2020-01-01T00:30:00", "2020-01-01T01:00:00", 109, 372],
   ["2020-01-01T00:30:00", "2020-01-01T01:30:00", 102, 378],
   ["2020-01-01T01:00:00", "2020-01-01T01:30:00", 101, 382],
   ["2020-01-01T01:00:00", "2020-01-01T02:00:00",  88, 398],
], columns=["req_time", "forecast_time", "solar", "wind"])
forecast = forecast.set_index(["req_time", "forecast_time"])
signal = vs.Trace(actual, forecast)

In [11]:
signal.forecast("2020-01-01T00:00:00", end_time="2020-01-01T01:00:00", column="solar")

{np.datetime64('2020-01-01T00:30:00.000000000'): np.float64(115.0),
 np.datetime64('2020-01-01T01:00:00.000000000'): np.float64(108.0)}

## Using Signals in Co-Simulations

Signals become powerful when used with Actors in co-simulations

In [16]:
environment = vs.Environment(sim_start="2022-06-15", step_size=300)  # 5-minute steps
environment.add_microgrid(
    actors=[
        # Server with 700W consumption
        vs.Actor(name="server", signal=vs.StaticSignal(value=-700)),
        # Solar panel using real Berlin weather data
        vs.Actor(name="solar", signal=vs.Trace.load("solcast2022_global", "Berlin", params={"scale": 5000})),
    ],
    storage=vs.SimpleBattery(capacity=1500),
)
environment.run(until=24 * 3600)  # 24 hours

2025-07-31 16:38:21.927 | INFO     | mosaik.async_scenario:start:420 - Starting "Actor" as "microgrid_5050938176.actor.server" ...
2025-07-31 16:38:21.928 | INFO     | mosaik.async_scenario:start:420 - Starting "Actor" as "microgrid_5050938176.actor.solar" ...
2025-07-31 16:38:21.929 | INFO     | mosaik.async_scenario:start:420 - Starting "Grid" as "microgrid_5050938176.grid" ...
2025-07-31 16:38:21.930 | INFO     | mosaik.async_scenario:start:420 - Starting "Storage" as "microgrid_5050938176.storage" ...
2025-07-31 16:38:21.932 | INFO     | mosaik.async_scenario:run:789 - Starting simulation.
100%|██████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 86400/86400 [00:00<00:00, 678663.28steps/s]
2025-07-31 16:38:22.060 | INFO     | mosaik.async_scenario:run:845 - Simulation finished successfully.
